In [1]:
from __future__ import print_function

import h5py 
import numpy as np

from IPython.display import Audio
import os, sys, random

from keras.models import Sequential
from keras.layers import Dense, Activation, LSTM
from helper import *

Using TensorFlow backend.
/home/shashwat/anaconda3/lib/python3.6/importlib/_bootstrap.py:205: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)


In [2]:
data_path = '/home/shashwat/Desktop/midi-rnn-master/data/midi/'

In [3]:
midis = [os.path.join(data_path,x) for x in os.listdir(data_path)]

In [4]:
len(midis)

183

In [5]:
batch_size = 32
seq_len = 30
vocab_size = 129 

In [6]:
def RNN(batch_size, seq_len):
    model = Sequential()
    model.add(LSTM(128, dropout=0.25, input_shape=(seq_len, vocab_size), return_sequences=True))
    model.add(LSTM(128, dropout=0.5, return_sequences=False))
    model.add(Dense(vocab_size))
    model.add(Activation('softmax'))
    return model

In [7]:
def train(model, batch_size, seq_len):
    model.compile(optimizer='adam', loss='categorical_crossentropy')
    
    idx = int(len(midis) * 0.2)

    train_gen = data_gen(midis[idx:], batch_size, seq_len, 1, 1)
    val_gen = data_gen(midis[:idx], batch_size, seq_len, 1, 1)
    
    model.fit_generator(train_gen, 
                        steps_per_epoch=len(midis) * 0.8 * 827 // batch_size, 
                        epochs=10, 
                        validation_data=val_gen, 
                        validation_steps= len(midis) * 0.2 * 827 // batch_size,                      
                        verbose=2, 
                        shuffle=True)
    return model          

In [10]:
model = RNN(batch_size, seq_len)
model.summary()

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
lstm_1 (LSTM)                (None, 30, 128)           132096    
_________________________________________________________________
lstm_2 (LSTM)                (None, 128)               131584    
_________________________________________________________________
dense_1 (Dense)              (None, 129)               16641     
_________________________________________________________________
activation_1 (Activation)    (None, 129)               0         
Total params: 280,321
Trainable params: 280,321
Non-trainable params: 0
_________________________________________________________________


In [11]:
model = train(model, batch_size, seq_len)

Epoch 1/10
 - 225s - loss: 2.8787 - val_loss: 4.2956
Epoch 2/10
 - 215s - loss: 2.8594 - val_loss: 3.9671
Epoch 3/10
 - 214s - loss: 2.6284 - val_loss: 3.3229
Epoch 4/10
 - 214s - loss: 2.3120 - val_loss: 2.9559
Epoch 5/10
 - 214s - loss: 2.0148 - val_loss: 1.9182
Epoch 6/10
 - 214s - loss: 1.8686 - val_loss: 2.3178
Epoch 7/10
 - 214s - loss: 1.8239 - val_loss: 1.6689
Epoch 8/10
 - 214s - loss: 1.7844 - val_loss: 2.1417
Epoch 9/10
 - 214s - loss: 1.6696 - val_loss: 1.7449
Epoch 10/10
 - 214s - loss: 1.7293 - val_loss: 1.7708


In [12]:
save_model(model, path='./')

Model Saved.


In [8]:
model = load_model('./')

Model Loaded.


In [42]:
idx = int(len(midis) * 0.1) # TODO: Choose Randomly
test_gen = data_gen(midis[:idx], batch_size, seq_len, 1, 1)

for i in range(random.randint(idx//2, idx)):
    prime, _ = next(test_gen)

In [53]:
path = 'gen1.mid'
length = 512

out = generate(model, prime, length)
midi = write_midi(out,'Electric Guitar (clean)',path=path)

In [55]:
y = midi.synthesize(fs = 16000)

In [56]:
Audio(y, rate=16000)

In [54]:
midi.instruments[0].notes

[Note(start=30.750000, end=31.000000, pitch=0, velocity=127),
 Note(start=46.750000, end=47.250000, pitch=60, velocity=127),
 Note(start=47.250000, end=47.500000, pitch=64, velocity=127),
 Note(start=47.500000, end=47.750000, pitch=0, velocity=127),
 Note(start=48.000000, end=48.500000, pitch=58, velocity=127),
 Note(start=48.500000, end=48.750000, pitch=64, velocity=127),
 Note(start=48.750000, end=49.000000, pitch=68, velocity=127),
 Note(start=49.000000, end=49.250000, pitch=71, velocity=127),
 Note(start=49.250000, end=49.500000, pitch=64, velocity=127),
 Note(start=49.500000, end=49.750000, pitch=60, velocity=127),
 Note(start=49.750000, end=50.000000, pitch=0, velocity=127),
 Note(start=51.500000, end=51.750000, pitch=84, velocity=127),
 Note(start=51.750000, end=52.000000, pitch=0, velocity=127),
 Note(start=52.750000, end=53.000000, pitch=0, velocity=127),
 Note(start=55.250000, end=55.500000, pitch=72, velocity=127),
 Note(start=55.500000, end=55.750000, pitch=77, velocity=127

In [47]:
midi.write(path)

In [49]:
Midi.INSTRUMENT_MAP

['Acoustic Grand Piano',
 'Bright Acoustic Piano',
 'Electric Grand Piano',
 'Honky-tonk Piano',
 'Electric Piano 1',
 'Electric Piano 2',
 'Harpsichord',
 'Clavinet',
 'Celesta',
 'Glockenspiel',
 'Music Box',
 'Vibraphone',
 'Marimba',
 'Xylophone',
 'Tubular Bells',
 'Dulcimer',
 'Drawbar Organ',
 'Percussive Organ',
 'Rock Organ',
 'Church Organ',
 'Reed Organ',
 'Accordion',
 'Harmonica',
 'Tango Accordion',
 'Acoustic Guitar (nylon)',
 'Acoustic Guitar (steel)',
 'Electric Guitar (jazz)',
 'Electric Guitar (clean)',
 'Electric Guitar (muted)',
 'Overdriven Guitar',
 'Distortion Guitar',
 'Guitar Harmonics',
 'Acoustic Bass',
 'Electric Bass (finger)',
 'Electric Bass (pick)',
 'Fretless Bass',
 'Slap Bass 1',
 'Slap Bass 2',
 'Synth Bass 1',
 'Synth Bass 2',
 'Violin',
 'Viola',
 'Cello',
 'Contrabass',
 'Tremolo Strings',
 'Pizzicato Strings',
 'Orchestral Harp',
 'Timpani',
 'String Ensemble 1',
 'String Ensemble 2',
 'Synth Strings 1',
 'Synth Strings 2',
 'Choir Aahs',
 'Voic